In [1]:
import torch
import torchvision
from torchvision import transforms, datasets, models
from torchvision.utils import save_image, make_grid

from torchviz import make_dot

import torch.optim as optim


import torch.nn as nn
import torch.nn.functional as F

import numpy as np
import math


import os 
import glob
import time
import cv2

from tqdm.notebook import tqdm
import pandas as pd
import matplotlib.pyplot as plt

import imageio

import enum

In [2]:
#TODO HERE
#implement IOmode auto inferred from input data shape

In [3]:
torch.cuda.is_available()
device = torch.device("cuda")

In [4]:
#hyperparams & options

EPOCHS = 200
lrD = 0.0004
lrG = 0.0002
bs = 2  #https://github.com/junyanz/pytorch-CycleGAN-and-pix2pix/issues/27#issuecomment-346495489
loss_fn = nn.BCELoss().to(device)
loss_fn_img = nn.L1Loss().to(device)
LAMBDA = 100

labelSmoothingFactor = 0.08
flip_labels = True
training_set_size = 865 - 15



In [5]:
class Dsk(nn.Module):
    
    def __init__(self, d=64):
        super(Dsk, self).__init__()        
                
        self.conv1 = nn.Conv2d(2, d, 4, 2, 1)
        self.conv2 = nn.Conv2d(d, d * 2, 4, 2, 1)
        self.conv2_bn = nn.BatchNorm2d(d * 2)
        self.conv3 = nn.Conv2d(d * 2, d * 4, 4, 2, 1)
        self.conv3_bn = nn.BatchNorm2d(d * 4)
        self.conv4 = nn.Conv2d(d * 4, d * 8, 4, 1, 1)
        self.conv4_bn = nn.BatchNorm2d(d * 8)
        self.conv5 = nn.Conv2d(d * 8, 1, 4, 1, 1)
        
        
        
    def forward(self, x):
        x = F.leaky_relu(self.conv1(x), 0.2)
        x = F.leaky_relu(self.conv2_bn(self.conv2(x)), 0.2)
        x = F.leaky_relu(self.conv3_bn(self.conv3(x)), 0.2)
        x = F.leaky_relu(self.conv4_bn(self.conv4(x)), 0.2)
        x = self.conv5(x)

        return torch.sigmoid(x)

    

In [8]:
#PASTED CODE
#https://github.com/znxlwm/pytorch-pix2pix/blob/master/network.py
#too difficult to follow the whole architecture, i understand what some blocks do

class Generator(nn.Module):
    def __init__(self, in_channels, out_channels):
        super(Generator, self).__init__()
        
        #reduce to features
        self.c0 = nn.Conv2d(in_channels, 64, 4, stride=2, padding=1)
        self.c1 = nn.Conv2d(64, 128, 4, stride=2, padding=1)
        self.c2 = nn.Conv2d(128, 256, 4, stride=2, padding=1)
        self.c3 = nn.Conv2d(256, 512, 4, stride=2, padding=1)
        self.c4 = nn.Conv2d(512, 512, 4, stride=2, padding=1)
        self.c5 = nn.Conv2d(512, 512, 4, stride=2, padding=1)
        self.c6 = nn.Conv2d(512, 512, 4, stride=2, padding=1)
        self.c7 = nn.Conv2d(512, 512, 4, stride=2, padding=1)
        
        #upsample to image
        self.d7 = nn.ConvTranspose2d(512, 512, 4, stride=2, padding=1)
        self.d6 = nn.ConvTranspose2d(1024, 512, 4, stride=2, padding=1)
        self.d5 = nn.ConvTranspose2d(1024, 512, 4, stride=2, padding=1)
        self.d4 = nn.ConvTranspose2d(1024, 512, 4, stride=2, padding=1)
        self.d3 = nn.ConvTranspose2d(1024, 256, 4, stride=2, padding=1)
        self.d2 = nn.ConvTranspose2d(512, 128, 4, stride=2, padding=1)
        self.d1 = nn.ConvTranspose2d(256, 64, 4, stride=2, padding=1)
        self.d0 = nn.ConvTranspose2d(128, out_channels, 4, stride=2, padding=1)
       
        self.bnc1 = nn.BatchNorm2d(128)
        self.bnc2 = nn.BatchNorm2d(256)
        self.bnc3 = nn.BatchNorm2d(512)
        self.bnc4 = nn.BatchNorm2d(512)
        self.bnc5 = nn.BatchNorm2d(512)
        self.bnc6 = nn.BatchNorm2d(512)

        self.bnd7 = nn.BatchNorm2d(512)
        self.bnd6 = nn.BatchNorm2d(512)
        self.bnd5 = nn.BatchNorm2d(512)
        self.bnd4 = nn.BatchNorm2d(512)
        self.bnd3 = nn.BatchNorm2d(256)
        self.bnd2 = nn.BatchNorm2d(128)
        self.bnd1 = nn.BatchNorm2d(64)
        
    def forward(self, x):           
        en0 = self.c0(x)
        en1 = self.bnc1(self.c1(F.leaky_relu(en0, negative_slope=0.2)))
        en2 = self.bnc2(self.c2(F.leaky_relu(en1, negative_slope=0.2)))
        en3 = self.bnc3(self.c3(F.leaky_relu(en2, negative_slope=0.2)))
        en4 = self.bnc4(self.c4(F.leaky_relu(en3, negative_slope=0.2)))
        en5 = self.bnc5(self.c5(F.leaky_relu(en4, negative_slope=0.2)))
        en6 = self.bnc6(self.c6(F.leaky_relu(en5, negative_slope=0.2)))
        en7 = self.c7(F.leaky_relu(en6, negative_slope=0.2))

        de7 = self.bnd7(self.d7(F.relu(en7)))
        de6 = F.dropout(self.bnd6(self.d6(F.relu(torch.cat((en6, de7),1)))))
        de5 = F.dropout(self.bnd5(self.d5(F.relu(torch.cat((en5, de6),1)))))

        de4 = F.dropout(self.bnd4(self.d4(F.relu(torch.cat((en4, de5),1)))))
        de3 = self.bnd3(self.d3(F.relu(torch.cat((en3, de4),1))))
        de2 = self.bnd2(self.d2(F.relu(torch.cat((en2, de3),1))))
        de1 = self.bnd1(self.d1(F.relu(torch.cat((en1, de2),1))))

        de0 = torch.tanh(self.d0(F.relu(torch.cat((en0, de1),1))))       

        return de0


In [9]:
D = Dsk().to(device)
optimizerD = optim.Adam(D.parameters(), lr=lrD)

In [10]:
G = Generator(1,1).to(device)
optimizerG = optim.Adam(G.parameters(), lr=lrG)

In [19]:
G(torch.ones(1,1,512,256).cuda()).shape

torch.Size([1, 1, 512, 256])

In [9]:
#LOAD STATE DICTs IF CONTINUING TRAINING
'''
G.load_state_dict(torch.load(''))
D.load_state_dict(torch.load(''))
G.eval()
D.eval()
'''

"\nG.load_state_dict(torch.load(''))\nD.load_state_dict(torch.load(''))\nG.eval()\nD.eval()\n"

In [10]:
data = torch.tensor(np.load('dirty_test_data.npy')).float().to(device)
print(len(data))
#data is (N, outchannels + inchannels, height, width)

865


In [11]:
trainData = data[:training_set_size]
testData = data[training_set_size:]
testData.shape
trainData[:,0,:,:].unsqueeze(1).shape

torch.Size([850, 1, 256, 256])

In [12]:

if(flip_labels):    
    zeroLabel = torch.zeros(bs*900).to(device) + labelSmoothingFactor
    oneLabel = torch.ones(bs*900).to(device) - labelSmoothingFactor
else:
    zeroLabel = torch.ones(bs*900).to(device) - labelSmoothingFactor
    oneLabel = torch.zeros(bs*900).to(device) + labelSmoothingFactor


with open("pix2pixPlateGenLog.log", "w") as logfile:
    
    #creating image folder
    try:
        os.mkdir('./generated_images/')
    
    except Exception as e:
        print('Mkdir failed. %s. Reason: %s' % ('./generated_images/', e))
    
    
    #clearing image folder
    files = glob.glob('./generated_images/*')
    for file in files:
        os.remove(file)
    
    #clearing models folder
    files = glob.glob('./epochModelParamData/*')
    for file in files:
        os.remove(file)
        
    

    #logfile csv header
    logfile.write(f"time,D_loss_real,D_loss_fake,G_loss,epoch\n")
    
    for epoch in tqdm(range(EPOCHS)):
             
        for i in tqdm(range(0, training_set_size, bs)):

            batchOfRealPairs = trainData[i:i+bs]           #(bs, 2, 256, 256)
            batchOfRealImgs = batchOfRealPairs[:,0,:,:].unsqueeze(1)   #(bs, 1, 256, 256)
            batchOfOutlines = batchOfRealPairs[:,1,:,:].unsqueeze(1)   #(bs, 1, 256, 256)


            D.zero_grad()
            
            D_real = torch.flatten(D(batchOfRealPairs))
            D_loss_real = loss_fn(D_real, oneLabel)
            D_loss_real.backward()

            batchOfFakeImgs = G(batchOfOutlines)    #(bs, 1, 256, 256)
            batchOfFakePairs = torch.cat((batchOfFakeImgs, batchOfOutlines), 1)  #(bs, 2, 256, 256)
            D_fake = torch.flatten(D(batchOfFakePairs.detach()))  #https://github.com/pytorch/examples/issues/116
            D_loss_fake = loss_fn(D_fake, zeroLabel) #bce(bs,900 & bs, 900)
            D_loss_fake.backward()

            optimizerD.step()


            G.zero_grad()

            D_fake = torch.flatten(D(batchOfFakePairs)) 
            G_loss = loss_fn(D_fake, oneLabel) + LAMBDA*loss_fn_img(batchOfFakeImgs, batchOfRealImgs)
            G_loss.backward()

            optimizerG.step()
            
            
            #logging in a file and printing
            logfile.write(f"{round(time.time(), 4)},{round(D_loss_real.mean().item(), 3)},{round(D_loss_fake.mean().item(), 3)},{round(G_loss.mean().item(), 3)},{epoch}\n")
            print(f"{round(time.time(), 4):15} | {round(D_loss_real.mean().item(), 3):5} | {round(D_loss_fake.mean().item(), 3):5} | {round(G_loss.mean().item(), 3):7} | {epoch:03} | {i}\n")
            
        
        #save imagees generated from testset and save model state every epoch
        epochImagePath = f"./generated_images/{epoch}.png"
        with torch.no_grad():
            generated_images = G(testData[:,1,:,:].unsqueeze(1))
            image_pairs = torch.cat((testData[:,1,:,:].unsqueeze(1), generated_images), 3)
            image_pairs = make_grid(image_pairs, nrow = 3)
            u = image_pairs.cpu().numpy().astype(np.float32)
            u = np.rint(((u + 1)/2)*255).astype(np.uint8)
            u = u.transpose(1,2,0)
            imageio.imwrite(epochImagePath, u)
            if(epoch%25 == 5): #state dictionarys are crazy large
                torch.save(D.state_dict(), f"./epochModelParamData/D{epoch}.pth")
                torch.save(G.state_dict(), f"./epochModelParamData/G{epoch}.pth")
            
        

Mkdir failed. ./generated_images/. Reason: [WinError 183] Cannot create a file when that file already exists: './generated_images/'


1590860532.8917 | 0.845 | 0.591 |  83.028 | 000 | 0
1590860533.0921 | 0.532 | 1.145 |  84.535 | 000 | 2
1590860533.2837 | 0.737 | 1.329 |  65.991 | 000 | 4
1590860533.4752 | 0.759 | 0.888 |  70.253 | 000 | 6
1590860533.6647 | 0.784 | 0.673 |  63.556 | 000 | 8
1590860533.8532 | 0.871 | 0.619 |  59.899 | 000 | 10
1590860534.0437 | 0.905 | 0.613 |  56.682 | 000 | 12
1590860534.2342 | 0.826 | 0.583 |  53.538 | 000 | 14
1590860534.4237 | 0.787 | 0.629 |  55.675 | 000 | 16
1590860534.6142 | 0.702 | 0.702 |  54.705 | 000 | 18
1590860534.8037 |  0.61 | 0.748 |  50.895 | 000 | 20
1590860534.9942 | 0.602 | 0.781 |  50.242 | 000 | 22
1590860535.1857 | 0.596 | 0.807 |  48.857 | 000 | 24
1590860535.3752 | 0.609 | 0.771 |  47.369 | 000 | 26
1590860535.5666 | 0.633 | 0.698 |  45.446 | 000 | 28
1590860535.7561 | 0.692 | 0.664 |  43.733 | 000 | 30
1590860535.9486 | 0.706 | 0.619 |  44.747 | 000 | 32
1590860536.1411 | 0.715 | 0.582 |  41.175 | 000 | 34
1590860536.3317 | 0.697 | 0.601 |  41.549 | 000 | 3

1590860591.0074 | 0.338 | 0.457 |  15.646 | 000 | 606
1590860591.2011 | 0.787 | 0.341 |  16.645 | 000 | 608
1590860591.3977 | 0.347 | 0.364 |  15.667 | 000 | 610
1590860591.5902 | 0.311 | 0.474 |  15.241 | 000 | 612
1590860591.7836 |  0.32 | 0.434 |  17.271 | 000 | 614
1590860591.9791 | 0.329 | 0.401 |   14.49 | 000 | 616
1590860592.1706 | 0.349 |  0.32 |  20.011 | 000 | 618
1590860592.3641 | 0.471 | 0.316 |  16.169 | 000 | 620
1590860592.5546 | 0.456 | 0.303 |  16.471 | 000 | 622
 1590860592.746 | 0.364 | 0.392 |  21.455 | 000 | 624
1590860592.9372 |  0.34 | 0.511 |  18.001 | 000 | 626
1590860593.1326 | 0.325 | 0.358 |  15.432 | 000 | 628
1590860593.3281 | 0.311 | 0.454 |  12.392 | 000 | 630
1590860593.5179 |  0.35 | 0.354 |  16.424 | 000 | 632
1590860593.7111 | 0.305 | 0.333 |  17.873 | 000 | 634
1590860593.9036 | 0.392 | 0.506 |  16.528 | 000 | 636
1590860594.0951 |   0.3 |  0.36 |  23.157 | 000 | 638
1590860594.2876 | 1.003 |  0.32 |  18.962 | 000 | 640
1590860594.4791 | 0.302 |  0

1590860615.6626 | 0.397 |   0.3 |  21.163 | 001 | 0
 1590860615.855 | 0.295 |   0.3 |  13.862 | 001 | 2
1590860616.0465 | 0.314 | 0.296 |  24.631 | 001 | 4
1590860616.2412 | 0.336 | 0.464 |  14.403 | 001 | 6
1590860616.4347 | 0.326 | 0.326 |  15.437 | 001 | 8
1590860616.6262 | 0.383 | 0.327 |  13.446 | 001 | 10
1590860616.8177 | 0.315 |  0.32 |  18.398 | 001 | 12
1590860617.0093 | 0.344 | 0.569 |  17.666 | 001 | 14
1590860617.2028 | 0.318 |  0.37 |  32.402 | 001 | 16
1590860617.3933 | 0.379 |  0.29 |  15.172 | 001 | 18
1590860617.5868 | 0.319 | 0.355 |  17.346 | 001 | 20
1590860617.7792 | 0.433 | 0.307 |  19.419 | 001 | 22
1590860617.9717 | 0.302 | 0.315 |  17.874 | 001 | 24
1590860618.1642 | 0.309 | 0.316 |  21.213 | 001 | 26
1590860618.3577 | 0.324 | 0.316 |  16.053 | 001 | 28
1590860618.5502 | 0.296 | 0.293 |  20.476 | 001 | 30
1590860618.7407 | 0.312 | 0.291 |  19.985 | 001 | 32
1590860618.9341 | 0.308 | 0.338 |  14.734 | 001 | 34
1590860619.1266 | 0.302 | 0.311 |  20.202 | 001 | 3

1590860674.1423 | 0.296 | 0.289 |  13.148 | 001 | 606
1590860674.3347 | 0.296 | 0.292 |  14.927 | 001 | 608
1590860674.5282 | 0.285 |   0.3 |  13.085 | 001 | 610
1590860674.7207 | 0.283 |  0.32 |  13.439 | 001 | 612
1590860674.9132 | 0.284 | 0.289 |  15.719 | 001 | 614
1590860675.1087 | 0.284 | 0.287 |  13.396 | 001 | 616
1590860675.3011 | 0.299 | 0.294 |  18.676 | 001 | 618
1590860675.4926 |  0.29 | 0.296 |  15.621 | 001 | 620
1590860675.6899 | 0.283 | 0.298 |  15.401 | 001 | 622
1590860675.8832 | 0.284 | 0.289 |  22.154 | 001 | 624
1590860676.0777 | 0.284 | 0.291 |  18.017 | 001 | 626
1590860676.2742 |  0.29 | 0.291 |  15.486 | 001 | 628
1590860676.4696 | 0.292 | 0.285 |  11.336 | 001 | 630
1590860676.6631 | 0.282 |  0.29 |  14.218 | 001 | 632
1590860676.8556 | 0.285 | 0.289 |  15.723 | 001 | 634
1590860677.0471 | 0.284 | 0.287 |  15.671 | 001 | 636
1590860677.2396 | 0.283 | 0.287 |  21.208 | 001 | 638
1590860677.4331 | 0.602 | 0.287 |  18.299 | 001 | 640
1590860677.6286 | 0.302 | 0.

...

1590879206.0687 | 0.797 | 0.425 |   4.062 | 197 | 606
1590879206.2751 | 0.709 | 0.467 |   4.361 | 197 | 608
1590879206.4796 | 0.653 | 0.456 |   4.298 | 197 | 610
1590879206.6841 | 0.596 | 0.564 |   4.209 | 197 | 612
1590879206.8885 | 0.609 |  0.61 |   4.052 | 197 | 614
 1590879207.094 | 0.553 | 0.684 |   3.672 | 197 | 616
1590879207.3004 | 0.435 | 0.808 |   4.425 | 197 | 618
1590879207.5039 | 0.409 | 0.756 |   4.541 | 197 | 620
1590879207.7073 | 0.591 | 0.725 |   3.494 | 197 | 622
1590879207.9128 | 0.455 | 0.808 |   5.367 | 197 | 624
1590879208.1192 | 0.452 | 0.701 |   4.795 | 197 | 626
1590879208.3237 | 0.741 | 0.628 |   4.662 | 197 | 628
1590879208.5281 | 0.729 | 0.533 |    3.34 | 197 | 630
1590879208.7346 | 0.693 | 0.544 |   4.328 | 197 | 632
 1590879208.944 | 0.704 | 0.486 |    4.57 | 197 | 634
1590879209.1485 | 0.648 |  0.58 |   3.983 | 197 | 636
1590879209.3499 | 0.661 | 0.533 |   4.672 | 197 | 638
1590879209.5534 |  0.66 | 0.535 |   4.912 | 197 | 640
1590879209.7598 |  0.58 | 0.

1590879234.0149 | 0.411 | 0.544 |   5.876 | 198 | 0
1590879234.2138 | 0.779 | 0.573 |    3.56 | 198 | 2
1590879234.4083 | 0.627 | 0.684 |   5.325 | 198 | 4
1590879234.6047 | 0.651 | 0.556 |   3.839 | 198 | 6
1590879234.7992 | 0.624 | 0.524 |   3.918 | 198 | 8
1590879234.9937 | 0.732 | 0.613 |   4.249 | 198 | 10
1590879235.1872 | 0.545 | 0.652 |   4.824 | 198 | 12
1590879235.3827 | 0.436 | 0.785 |   4.247 | 198 | 14
1590879235.5781 | 0.384 | 0.991 |   6.657 | 198 | 16
1590879235.7766 | 0.376 | 0.786 |   3.549 | 198 | 18
1590879235.9721 | 0.365 | 0.875 |   4.316 | 198 | 20
1590879236.1666 | 0.605 | 0.694 |    4.25 | 198 | 22
  1590879236.36 |  0.56 | 0.576 |   4.378 | 198 | 24
1590879236.5555 |  0.52 | 0.468 |   5.641 | 198 | 26
 1590879236.751 | 0.805 |  0.42 |   4.183 | 198 | 28
1590879236.9495 | 0.868 | 0.405 |   4.779 | 198 | 30
 1590879237.144 | 1.026 |  0.39 |   4.537 | 198 | 32
1590879237.3394 |  0.86 | 0.423 |   4.175 | 198 | 34
1590879237.5359 | 1.055 | 0.366 |   5.184 | 198 | 3

1590879296.2587 | 0.856 | 0.448 |   3.993 | 198 | 606
1590879296.4611 | 0.705 | 0.452 |   4.302 | 198 | 608
1590879296.6706 | 0.673 | 0.453 |   4.066 | 198 | 610
1590879296.8761 | 0.571 | 0.601 |   3.919 | 198 | 612
1590879297.0805 | 0.578 | 0.722 |   4.046 | 198 | 614
 1590879297.289 | 0.563 | 0.701 |   3.617 | 198 | 616
1590879297.4974 | 0.427 | 0.856 |    4.23 | 198 | 618
1590879297.7059 | 0.438 | 0.927 |   4.418 | 198 | 620
1590879297.9133 | 0.607 |  0.72 |   3.394 | 198 | 622
1590879298.1227 | 0.488 | 0.765 |   5.131 | 198 | 624
1590879298.3342 |   0.4 | 0.689 |   4.782 | 198 | 626
1590879298.5446 | 0.707 | 0.622 |   4.616 | 198 | 628
1590879298.7501 | 0.707 | 0.553 |   3.274 | 198 | 630
1590879298.9575 | 0.636 |  0.51 |   4.346 | 198 | 632
1590879299.1649 | 0.685 | 0.436 |   4.525 | 198 | 634
1590879299.3724 |  0.63 | 0.571 |   4.024 | 198 | 636
1590879299.5759 | 0.673 | 0.471 |   4.679 | 198 | 638
1590879299.7803 | 0.629 | 0.484 |   5.039 | 198 | 640
1590879299.9868 | 0.579 | 0.

1590879323.5163 | 0.488 | 0.516 |     5.9 | 199 | 0
1590879323.7148 | 0.808 | 0.461 |   3.693 | 199 | 2
1590879323.9082 | 0.663 | 0.568 |   5.323 | 199 | 4
1590879324.1047 | 0.653 | 0.495 |   3.759 | 199 | 6
1590879324.3002 | 0.578 | 0.571 |   4.086 | 199 | 8
1590879324.4947 | 0.712 | 0.549 |   4.122 | 199 | 10
1590879324.6921 | 0.478 | 0.698 |   4.791 | 199 | 12
1590879324.8866 |  0.43 | 0.916 |   4.542 | 199 | 14
1590879325.0801 | 0.411 | 0.935 |   6.601 | 199 | 16
1590879325.2846 | 0.375 | 0.739 |   3.904 | 199 | 18
 1590879325.495 | 0.468 | 0.709 |   4.103 | 199 | 20
1590879325.7014 | 0.621 | 0.596 |   4.301 | 199 | 22
1590879325.9059 | 0.542 | 0.597 |   4.412 | 199 | 24
1590879326.1124 | 0.541 | 0.532 |   5.585 | 199 | 26
1590879326.3208 | 0.681 | 0.526 |   3.881 | 199 | 28
1590879326.5303 | 0.836 | 0.419 |   4.798 | 199 | 30
1590879326.7367 | 0.984 | 0.404 |   4.786 | 199 | 32
1590879326.9386 | 0.866 | 0.448 |   4.235 | 199 | 34
 1590879327.148 | 0.879 | 0.394 |   5.105 | 199 | 3

1590879386.5738 |   0.8 |  0.45 |   3.923 | 199 | 606
1590879386.7835 |   0.8 | 0.428 |    4.33 | 199 | 608
  1590879386.99 | 0.682 | 0.467 |   4.121 | 199 | 610
1590879387.1984 | 0.536 | 0.605 |   4.026 | 199 | 612
1590879387.4079 | 0.485 | 0.703 |   4.016 | 199 | 614
1590879387.6173 |  0.51 | 0.724 |   3.667 | 199 | 616
1590879387.8257 | 0.475 | 0.657 |   4.629 | 199 | 618
1590879388.0332 | 0.426 | 0.831 |   4.671 | 199 | 620
1590879388.2416 | 0.654 | 0.589 |   3.539 | 199 | 622
1590879388.4481 | 0.607 | 0.612 |    5.13 | 199 | 624
1590879388.6535 | 0.459 | 0.509 |   4.782 | 199 | 626
 1590879388.863 | 0.646 | 0.637 |   4.443 | 199 | 628
1590879389.0714 | 0.765 | 0.489 |   3.319 | 199 | 630
1590879389.2791 | 0.621 | 0.575 |    4.22 | 199 | 632
1590879389.4875 | 0.632 | 0.499 |   4.296 | 199 | 634
 1590879389.696 | 0.581 | 0.633 |   3.842 | 199 | 636
1590879389.9018 | 0.688 | 0.528 |   4.583 | 199 | 638
1590879390.1102 | 0.482 | 0.699 |   4.785 | 199 | 640
1590879390.3177 |  0.66 | 0.

In [16]:
#Creating a GIF

images = []
j = 0
for i in glob.glob("./generated_images/*"):    
    img = imageio.imread(i)
    #cv2.putText(image, text, org, font, fontScale, color[, thickness[, lineType[, bottomLeftOrigin]]])
    img = cv2.putText(img, str(j), (50, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, (255,255,0), 2, cv2.LINE_AA)
    images.append(img)
    j+=1
    

imageio.mimwrite("epochs.gif", images, fps = 50, loop = 0)    

In [31]:
netG = Generator(1,1).to(device)
netG.load_state_dict(torch.load('./epochModelParamData/G80.pth'))

pug = cv2.imread('./ThePugTest.png', cv2.IMREAD_GRAYSCALE)
pug = pug.astype(np.float32)
pug = pug/127.5 - 1 
pug = torch.tensor(pug).to(device)
pug = pug.unsqueeze(0).unsqueeze(0)
print(pug.shape)

pug_plate_of_truth = netG(pug)

pug_plate_of_truth = pug_plate_of_truth.squeeze(0).squeeze(0)
pug = pug.squeeze(0).squeeze(0)
pug_plate = torch.cat((pug,pug_plate_of_truth),1)
pug_plate = pug_plate.cpu().detach().numpy()

pug_plate = (pug_plate + 1)/2 *255
pug_plate = pug_plate.astype(np.uint8)
%matplotlib qt
plt.imshow(pug_plate, cmap="gray")
imageio.imwrite('pug_plate.png', pug_plate)

torch.Size([1, 1, 256, 256])


In [29]:
%matplotlib inline
df = pd.read_csv('pix2pixPlateGenLog.log')
df.rolling(window = 50)['G_loss'].plot()

KeyboardInterrupt: 

In [15]:
help(imageio.imwrite)

Help on function imwrite in module imageio.core.functions:

imwrite(uri, im, format=None, **kwargs)
    imwrite(uri, im, format=None, **kwargs)
    
    Write an image to the specified file.
    
    Parameters
    ----------
    uri : {str, pathlib.Path, file}
        The resource to write the image to, e.g. a filename, pathlib.Path
        or file object, see the docs for more info.
    im : numpy.ndarray
        The image data. Must be NxM, NxMx3 or NxMx4.
    format : str
        The format to use to read the file. By default imageio selects
        the appropriate for you based on the filename and its contents.
    kwargs : ...
        Further keyword arguments are passed to the writer. See :func:`.help`
        to see what arguments are available for a particular format.

